In [ ]:
import numpy as np
import matplotlib.pyplot as plt
import random
from scipy.spatial import distance
from matplotlib.animation import FFMpegWriter


In [ ]:
# CONSTANTS

WALL = (50, 50, 50)
EMPTY_SPACE = (250, 250, 250)
CURRENT_POSITION = (50, 135, 235)
SEAT = (250, 250, 0)
TAKEN_SEAT = (250, 0, 0)

In [ ]:
### Helper Functions

In [ ]:
def isSpaceOpen(position, board):
    
    pm_x, pm_y = position
    maxYRange, maxXRange= len(board), len(board[0])
    
    # Check if the position is out of bounds
    if (pm_x < 0 or pm_x >= maxXRange or pm_y < 0 or pm_y >= maxYRange):
        #print("The move was out of bounds")
        return False

    # Check if the position is a wall or already taken seat
    if ((board[pm_y, pm_x]==WALL).all() or (board[pm_y, pm_x]==TAKEN_SEAT).all()):
        #print("Detected hitting a wall")
        return False

    return True

In [ ]:
def generatePossibleMoves(currPosition, board, prevSpots):
    x, y = currPosition
    
    minXRange = 0
    minYRange = 0
    maxXRange = len(board[0])
    maxYRange = len(board)
    
    
    # Generating adjacent positions
    possibleMoves = [
        (x, y+1),
        (x+1, y),
        (x, y-1),
        (x-1, y),
    ]
    
    legalMoves = []
    # Check if possibleMoves are legal moves
    for pm in possibleMoves:
        #print(pm)
        
        pm_x, pm_y = pm
        
        if (not isSpaceOpen(pm, board)):
            continue
        
        # Check if the position was a prev position

        if (pm in prevSpots):
            #print("The move was already a previous position")
            continue
        
        
        
        # The move has passed all checks. The move is legal
        legalMoves.append(pm)
        
    return legalMoves

In [ ]:
def chooseMove(prevPosition, currPosition, legal_moves, board):
    
    legal_moves_count = len(legal_moves)
    
    # Only one move to take
    if (legal_moves_count == 1):
        return legal_moves[0]
    
    # If one of the moves is an open seat, take it
    
    for lm in legal_moves:
        if ((board[lm[1],lm[0]]==SEAT).all()):
            return lm
    
    
    x_vel = currPosition[0] - prevPosition[0]
    y_vel = currPosition[1] - prevPosition[1]
    
    # The desired_position is the position that keeps momentum
    desired_position = ((currPosition[0] + x_vel), (currPosition[1] + y_vel))
    
    
    
    probability_array = []
    #print("dp:", desired_position, "lm:", legal_moves)
    
    if (desired_position in legal_moves):
        desired_position_probability = .90 # Magic number
        undesired_position_probability = (1 - desired_position_probability) / (legal_moves_count - 1)
        
        
        probability_array = [undesired_position_probability] *  legal_moves_count
        dp_index = legal_moves.index(desired_position)
        probability_array[dp_index] = desired_position_probability
        
    else:
        #probability_array = [ 1 / legal_moves_count] *  legal_moves_count
        
        # Find which legal move has the most additional space to it and weight it more
        maxDist = -1
        #desired_move = None
        probability_array = []
        for lm in legal_moves:
            
            x_vel = lm[0] - currPosition[0]
            y_vel = lm[1] - currPosition[1]
            
            nextSpot = lm
            while(isSpaceOpen(nextSpot, board)):
                nextSpot = (nextSpot[0] + x_vel, nextSpot[1] + y_vel)
            
            
            dist = distance.euclidean(lm, nextSpot)
            """
            if (dist > maxDist):
                maxDist = dist
                desired_move = lm
            """
            probability_array.append(dist)
            
        
    
    """
    # generating random samples with probabilities
    print(np.random.choice(prog_langs, size=10,
                       replace=True, p=[0.3, 0.5, 0.0, 0.2]))
    """
    #print("CP:", currPosition)
    if (currPosition[0] == 11 and currPosition[1] == 5):
        print("At the expected position")
        print(legal_moves)
        print(probability_array)
    return random.choices(legal_moves, weights=probability_array, k=1)[0]
    
    #return legal_moves[np.random.choice(len(legal_moves))]

In [ ]:
def generateDefaultBoard():
    # Generate Board
    maxX = 50
    maxY = 50
    
    board = np.full((maxX, maxX, 3), 255, dtype='uint8')
    #np.zeros([maxY,maxX,3],dtype='uint8')
    
    board[7:20, 7:20] = WALL
    board[7:20, 30:42] = WALL
    board[30:42, 7:20] = WALL
    board[30:42, 30:42] = WALL
    
    return board

In [ ]:
def generate1951CoffeeBoard():
    # Generate Board
    maxX = 15
    maxY = 10
    
    board = np.full((maxY, maxX, 3), 255, dtype='uint8')
    #np.zeros([maxY,maxX,3],dtype='uint8')
    
    # Walls
    board[:, 0:3] = WALL  # Kitchen area
    board[8:, 3:6] = WALL
    board[0, 4] = WALL
    board[0, 7] = WALL
    
    # Seats
    board[0, 5:7] = SEAT # Seats against wall
    board[0, 8:11] = SEAT
    
    board[2, 7:9] = SEAT # Seats in the middle
    board[3, 6:8] = SEAT
    board[4, 5:7] = SEAT
    board[5, 5:7] = SEAT
    board[6, 6:8] = SEAT
    board[7, 7:9] = SEAT
    
    board[9, 11:] = SEAT # Seats in corner
    
    board[2, 13] = SEAT # Seats along right wall
    board[3, 12] = SEAT
    board[4, 12] = SEAT
    board[5, 13] = SEAT
    board[6, 14] = SEAT
    
    # Tables on right side
    board[2:6, 14] = WALL
    board[3:5, 13:] = WALL
    
    
    return board

In [ ]:
def generateSodoiBoard():
    # Generate Board
    maxX = 13
    maxY = 23
    
    board = np.full((maxY, maxX, 3), 255, dtype='uint8')
    
    # Walls
    board[6:, :6] = WALL 
    board[5:, :5] = WALL 
    board[4:, :4] = WALL
    board[6:8, 6] = WALL
    
    # Tables
    board[9:12:, 9] = WALL
    board[13:15:, 9] = WALL
    board[17:22:, 9] = WALL
    board[5, 12] = WALL
    
    # Seat
    board[0, 6:11] = SEAT # Lower seats
    board[1:5, 12] = SEAT
    board[6:8, 12] = SEAT
    board[6:8, 7] = SEAT
    
    # Middle Seats
    board[9:12, 8] = SEAT
    board[9:12, 10] = SEAT
    board[13:15, 8] = SEAT
    board[13:15, 10] = SEAT
    board[17:22, 8] = SEAT
    board[17:22, 10] = SEAT
    
    # Wall Seats
    board[15:, 6] = SEAT
    board[22, 12] = SEAT
    board[20, 12] = SEAT
    board[18, 12] = SEAT
    
    
    
    return board

In [ ]:
def generateMLKBoard():
    # Generate MLK 2nd Floor
    maxX = 35
    maxY = 35
    
    board = np.full((maxY, maxX, 3), 255, dtype='uint8')
    board[25:, :27] = WALL
    board[21:25, :13] = WALL
    board[13:20, 17:30] = WALL
    
    board[2, 16] = SEAT # Back wall
    board[0, 17] = SEAT
    board[2, 18] = SEAT
    board[2, 20] = SEAT
    board[0, 21] = SEAT
    board[2, 22] = SEAT
    board[2, 24] = SEAT
    board[0, 25] = SEAT
    board[2, 26] = SEAT
    board[2, 28] = SEAT
    board[0, 29] = SEAT
    board[2, 30] = SEAT
    board[2, 32] = SEAT
    board[0, 33] = SEAT
    board[2, 34] = SEAT
    
    board[6,6] = SEAT # Left window seats
    board[7,5] = SEAT
    board[8,6] = SEAT
    board[7,7] = SEAT
    board[10,6] = SEAT
    board[11,5] = SEAT
    board[12,6] = SEAT
    board[11,7] = SEAT
    board[14,6] = SEAT
    board[15,5] = SEAT
    board[16,6] = SEAT
    board[15,7] = SEAT

    board[6,11] = SEAT 
    board[7,10] = SEAT
    board[8,11] = SEAT
    board[7,12] = SEAT
    board[10,11] = SEAT
    board[11,10] = SEAT
    board[12,11] = SEAT
    board[11,12] = SEAT
    board[14,11] = SEAT
    board[15,10] = SEAT
    board[16,11] = SEAT
    board[15,12] = SEAT
    
    board[6,0] = SEAT
    board[8,1] = SEAT
    board[6,2] = SEAT
    
    board[10,0] = SEAT
    board[12,1] = SEAT
    board[10,2] = SEAT
    
    board[14,0] = SEAT
    board[16,1] = SEAT
    board[14,2] = SEAT
    
    board[18,0] = SEAT
    board[20,1] = SEAT
    board[18,2] = SEAT
    
    board[20,5] = SEAT
    board[19,6] = SEAT
    board[20,7] = SEAT
    
    board[20,10] = SEAT
    board[19,11] = SEAT
    board[20,12] = SEAT
    
    board[6,18] = SEAT 
    board[7,17] = SEAT
    board[8,18] = SEAT
    board[7,19] = SEAT
    board[10,18] = SEAT
    board[11,17] = SEAT
    board[12,18] = SEAT
    board[11,19] = SEAT
    
    board[6,23] = SEAT 
    board[7,22] = SEAT
    board[8,23] = SEAT
    board[7,24] = SEAT
    board[10,23] = SEAT
    board[11,22] = SEAT
    board[12,23] = SEAT
    board[11,24] = SEAT
    
    board[6,28] = SEAT 
    board[7,27] = SEAT
    board[8,28] = SEAT
    board[7,29] = SEAT
    board[10,28] = SEAT
    board[11,27] = SEAT
    board[12,28] = SEAT
    board[11,29] = SEAT
    
    
    board[5, 32] = SEAT
    board[6, 34] = SEAT
    board[7, 32] = SEAT
    board[9, 32] = SEAT
    board[10, 34] = SEAT
    board[11, 32] = SEAT
    board[13, 32] = SEAT
    board[14, 34] = SEAT
    board[15, 32] = SEAT
    board[17, 32] = SEAT
    board[18, 34] = SEAT
    board[19, 32] = SEAT
    
    board[24, 28] = SEAT
    board[26, 27] = SEAT
    board[26, 29] = SEAT
    
    board[28, 28] = SEAT
    board[30, 27] = SEAT
    board[30, 29] = SEAT
    
    board[32, 28] = SEAT
    board[34, 27] = SEAT
    board[34, 29] = SEAT
    
    
    return board


In [ ]:
def generateKresgeBoard():
    # Generate Kresge 1st Floor
    maxX = 35
    maxY = 40
    
    board = np.full((maxY, maxX, 3), 255, dtype='uint8')
    
    board[:10, 13:20] = WALL
    board[:15, 24:] = WALL
    board[17, 24:33] = WALL
    board[:15, 12] = WALL
    
    # Bookshelves
    board[3, 1:10] = WALL
    board[5, 1:10] = WALL
    board[7, 1:10] = WALL
    board[9, 4:10] = WALL
    board[11, 4:10] = WALL
    board[13, 4:10] = WALL
    board[15, 4:10] = WALL
    board[17, 2:10] = WALL
    board[19, 2:10] = WALL
    board[21, 2:10] = WALL
    board[23, 2:10] = WALL
    
    board[11:15, 21] = WALL
    board[16, 12:20] = WALL
    board[16:24, 11] = WALL
    
    # Mid-north bookshelves
    board[28:33, 9] = WALL
    board[28:33, 11] = WALL
    board[28:33, 13] = WALL
    board[28:33, 15] = WALL
    board[28:33, 17] = WALL
    board[28:33, 19] = WALL
    board[28:33, 21] = WALL
    board[28:33, 23] = WALL
    board[28:33, 25] = WALL
    board[28:33, 27] = WALL
    
    board[28:33, 27:33] = WALL

    
    
    board[11:14, 19] = SEAT
    board[10, 18] = SEAT
    board[10, 15] = SEAT
    board[10, 13] = SEAT
    board[10,14] = WALL
    board[14, 13] = SEAT
    board[14,14] = WALL
    board[14, 15] = SEAT
    
    board[16:19, 20] = WALL
    board[25, 13:21] = WALL
    board[22:25, 20] = WALL
    
    board[18:21, 17:19] = SEAT # Seats on the mid-left
    board[18:21,13:15] = SEAT
    board[22:25, 13:15] = SEAT
    board[22:25, 17:19] = SEAT
    
    board[18:21, 25:27] = SEAT # Seats on the mid-right
    board[22:25, 25:27] = SEAT
    board[18:21, 28:30] = SEAT
    board[22:25, 28:30] = SEAT
    board[18:21, 31:33] = SEAT
    board[22:25, 31:33] = SEAT
    
    board[19, 34] = SEAT # Seats all the way to the right
    board[21, 34] = SEAT 
    board[23, 34] = SEAT
    board[25, 34] = SEAT
    board[27, 34] = SEAT 
    
    board[9, 0:2] = SEAT # Seats all the way to the left
    board[10, 0:2] = WALL
    board[11, 0:2] = SEAT

    board[13, 0:2] = SEAT
    board[14, 0:2] = WALL
    board[15, 0:2] = SEAT
    
    board[18, 0] = SEAT
    board[19, 0] = WALL
    board[20, 0] = SEAT
    board[21, 0] = WALL
    board[22, 0] = SEAT
    board[23:25, 0] = WALL
    board[25, 0] = SEAT
    
    board[26:29, 1] = SEAT
    board[26:29, 3] = SEAT
    board[26:29, 5] = SEAT
    board[26:29, 7] = SEAT
    
    board[30:33, 1] = SEAT
    board[30:33, 3] = SEAT
    board[30:33, 5] = SEAT
    board[30:33, 7] = SEAT
    
    board[33, 0] = SEAT
    
    board[34:38, 9] = SEAT # Mid-north seat
    board[34:38, 10] = WALL 
    board[34:38, 11] = SEAT 
    
    board[34:38, 13] = SEAT
    board[34:38, 14] = WALL 
    board[34:38, 15] = SEAT 
    
    board[34:38, 17] = SEAT
    board[34:38, 18] = WALL 
    board[34:38, 19] = SEAT 
    
    board[34:38, 21] = SEAT
    board[34:38, 22] = WALL 
    board[34:38, 23] = SEAT 
    
    board[35:38, 1] = WALL # North Bookshelves
    board[34:38, 3] = WALL
    board[34:38, 25] = WALL 
    board[34:38, 27] = WALL 
    board[34:38, 29] = WALL 
    board[34:38, 31] = WALL 
    board[34:38, 33] = WALL
    
    board[39, 0:3] = WALL
    board[39, 3] = SEAT
    board[39, 4] = WALL
    board[39, 5] = SEAT
    board[39, 6] = WALL
    board[39, 7] = SEAT
    board[39, 8] = WALL
    board[39, 9:11] = SEAT
    board[39, 11] = WALL
    board[39, 12:14] = SEAT
    board[39, 14] = WALL
    board[39, 15:17] = SEAT
    board[39, 17] = WALL
    board[39, 18:20] = SEAT
    board[39, 20] = WALL
    board[39, 21:23] = SEAT
    
    board[39, 25] = WALL
    board[39, 26] = SEAT
    board[39, 27] = WALL
    board[39, 28] = SEAT
    board[39, 29] = WALL
    board[39, 30] = SEAT
    board[39, 31] = WALL
    board[39, 32] = SEAT
    
    return board

In [ ]:
def display(brd):
    
    flip_brd = np.flip(brd, 0)
    
    #plt.rcParams['figure.figsize'] = [6, 6/maxX*maxY]
    plt.imshow(flip_brd); 
    #plt.axis('off'); 
    #plt.show()
    plt.draw()
    #plt.pause(0.01)
    
    
def numOfOpenSeats(board):
    open_seats = 0
    
    for row in board:
        for position in row:
            if ((position==SEAT).all()):
                open_seats += 1
            
    return open_seats

In [ ]:
def runSimulation(board, position, prevPosition, num_of_students, Title):
    
    %matplotlib osx
    metadata = dict(title='Simulation for eps109', artist='Matplotlib',comment='wah')
    writer = FFMpegWriter(fps=15, metadata=metadata,bitrate=200000)
    fig = plt.figure(dpi=200)
    plt.title(Title)
    with writer.saving(fig, Title + ".mp4", dpi=200):
        for n in range(num_of_students):
            runStudentWalk(board, position, prevPosition, writer)
            fig.clear()
    
def runStudentWalk(board, position, prevPosition, writer):    
    # Helps establish momentum
    x, y = position

    board[y, x] = CURRENT_POSITION

    prevSpots = set()
    prevSpots.add(position)

    for i in range(1000):
        legal_moves = generatePossibleMoves(position, board, prevSpots)
        # print(legal_moves)

        # Got itself stuck
        if (len(legal_moves) == 0):
            print("The student got stuck, must quit")
            break

        """
        # Zero out old position
        x, y = position
        board[y, x] = EMPTY_SPACE
        """

        # Generate new position and update board and update prevSpots    
        newPosition = chooseMove(prevPosition, position, legal_moves, board)
        prevPosition = position
        position = newPosition
        x, y = position

        # If new position is an open seat, terminate
        if ((board[y, x] ==SEAT).all()):
            board[y, x] = TAKEN_SEAT
            display(board)
            break


        # CURRENT_POSITION += .01
        board[y, x] = CURRENT_POSITION
        prevSpots.add(position)


        # Update graphics
        display(board)
        writer.grab_frame()
        
    # Cleanup board
    for pos in prevSpots:
        board[pos[1], pos[0]] = EMPTY_SPACE
    display(board)

In [ ]:
# Run 1951 Simulation
board1951 = generate1951CoffeeBoard()
numOfOpenSeatsInitial = numOfOpenSeats(board1951)
runSimulation(board1951, (3,0), (3,1), numOfOpenSeatsInitial * 2, "1951 Coffee Simulation")
numOfOpenSeatsFinal = numOfOpenSeats(board1951)
print("Space Effectiveness:", (numOfOpenSeatsInitial - numOfOpenSeatsFinal) / numOfOpenSeatsInitial)

In [ ]:
# Run Sodoi Simulation
sodoiBoard = generateSodoiBoard()
numOfOpenSeatsInitial = numOfOpenSeats(sodoiBoard)
runSimulation(sodoiBoard, (3,0), (3,1), numOfOpenSeatsInitial * 2, "Sodoi Simulation")
numOfOpenSeatsFinal = numOfOpenSeats(sodoiBoard)
print("Space Effectiveness:", (numOfOpenSeatsInitial - numOfOpenSeatsFinal) / numOfOpenSeatsInitial)

In [ ]:
# Run MLK Simulation
MLKboard = generateMLKBoard()
numOfOpenSeatsInitial = numOfOpenSeats(MLKboard)
runSimulation(MLKboard, (15,0), (15,1), 100, "MLK 1st Floor Simulation")
numOfOpenSeatsFinal = numOfOpenSeats(MLKboard)
print("Space Effectiveness:", (numOfOpenSeatsInitial - numOfOpenSeatsFinal) / numOfOpenSeatsInitial)

In [ ]:
# Run Kresge Simulation
kresgeBoard = generateKresgeBoard()
numOfOpenSeatsInitial = numOfOpenSeats(kresgeBoard)
runSimulation(kresgeBoard, (22,9), (22,8), 100, "Kresge 1st Floor Simulation")
numOfOpenSeatsFinal = numOfOpenSeats(kresgeBoard)
print("Space Effectiveness:", (numOfOpenSeatsInitial - numOfOpenSeatsFinal) / numOfOpenSeatsInitial)